In [1]:
import os,sys
from bs4 import BeautifulSoup as bs
import requests
import threading
from time import sleep
import json

## Utilities

In [2]:
def cleanText(text):
    '''
        Don't do much pre processing. Important info might get lost.
    '''
    text = text.strip()
    return text

## Logging

In [3]:
DATA_PATH = "./data"
skipped_pages_log = open('./logs/skipped_files.txt','w')

## Setting up variables for multi-theading

In [4]:
NUM_MOVIE_THREADS = 4
NUM_WRITER_THREADS = 4

In [5]:
semaphore = threading.Semaphore()

## Get data from the movie list

In [6]:
url = 'https://www.lyricsmasti.com/song/7461/lyrics-of-Dil-Kashi.html'
soup = bs(requests.get(url).text,"lxml")

In [7]:
def getMovieList(soup):
    movie_list = soup.find_all('ul',class_='list-group list-group-flush')[0].find_all('a')
    view_list = soup.find_all('li',class_='list-group-item')
    movie_list_data = []
    assert len(movie_list) == len(view_list), "#movies != #views"
    for i in range(len(movie_list)):
        movie_name_list = movie_list[i].get_text().split("-")
        movie_year = -1
        if len(movie_name_list) >= 2:
            movie_year = cleanText(movie_name_list[1])
        movie_list_data.append({"url":movie_list[i]['href'],"views":view_list[i]['title'],"movie_name":cleanText(movie_list[i].get_text()),"movie_year":movie_year})
    return movie_list_data

In [8]:
def getSongList(soup):
    song_list = soup.find_all('ol',class_='custom-counter')[0].find_all('a')
    song_list_data = []
    for song in song_list:
        song_list_data.append({'song_url':song['href'],'song_name':cleanText(song.get_text())})
    return song_list_data

In [9]:
def getSongData(soup):
    song_data = {}
    lyrics = soup.find_all('code')[0].get_text()
    song_data.update({'song_lyrics':lyrics})

    song_informtion = soup.find_all('li',class_='f-w')[0].find_all('ul')[0].find_all('li')
    for info in song_informtion:
        property_val = -1
        property_name = "unk"
        if len(info.find_all('h4')) >= 1:
            #print(cleanText(info.find_all('h4')[0].get_text()))
            property_name = cleanText(info.find_all('h4')[0].get_text())
        if len(info.find_all('span')) >= 1:
            #print(cleanText(info.find_all('span')[0].get_text()))
            property_val = cleanText(info.find_all('span')[0].get_text())
        elif len(info.find_all('p')) >= 1:
            #print(cleanText(info.find_all('p')[0].get_text()))
            property_val = cleanText(info.find_all('p')[0].get_text())
        if property_name != "unk":
            song_data.update({property_name:property_val})
            
    return song_data


In [10]:
def getAllSongsFromAMovie(base_url,movie,skipped_pages_log):
    
    
    print("Processing movie: ",movie['movie_name'])
    song_page_url = base_url+movie['url']
    print("song_page_url: {}".format(song_page_url))
    try:
        song_soup = bs(requests.get(song_page_url).text,"lxml")
    except:
        skipped_pages_log.write(song_page_url)
        print("skipped song page: ",song_page_url)
        continue

    song_list_data = getSongList(song_soup)
    print(song_list_data)
    song_data_list = []
    for song in song_list_data:
        print("Processing movie: ",song['song_name'])
        song_url = base_url+song['song_url']
        print("song_url: {}".format(song_url))
        try:
            song_data_soup = bs(requests.get(song_url).text,"lxml")
        except:
            skipped_pages_log.write(song_url)
            print("skipped song page: ",song_url)
            continue
        song_data = getSongData(song_data_soup)
        print(song_data)
        song_data_list.append(song_data)
        
    #Write Data to a movie named folder
    os.mkdir(os.path.join(DATA_PATH,movie['movie_name']))
    for song in song_data_list:
        for k,v in movie.items():
            song.update({k:v})
        
        

SyntaxError: 'continue' not properly in loop (<ipython-input-10-555e8750240f>, line 12)

## Data Extraction Loop

In [ ]:
base_url = 'https://www.lyricsmasti.com'
num_chars = 26
for i in range(num_chars):
    movie_page_base_url = base_url+'/songs_for_movie_'+chr(ord('A')+i)+'.html'
    print("Processing: {}".format(movie_page_base_url))
    
    page_num = 0
    while True:
        if page_num > 0:
            cur_page_url = movie_page_base_url+"?page="+str(page_num)
        else:
            cur_page_url = movie_page_base_url
        print(cur_page_url)
        
        try:
            soup = bs(requests.get(cur_page_url).text,"lxml")
        except:
            skipped_pages_log.write(cur_page_url)
            print("skipped page: ",cur_page_url)
            continue
        
        #Process data
        movie_data = getMovieList(soup)
        print("No. of song movies in this page:",len(movie_data))
        #Terminating condition
        if len(movie_data) == 0:
            break
            
        for movie in movie_data:
            #Create a  thread here to get data for an individual movie
            print("Processing movie: ",movie['movie_name'])
            song_page_url = base_url+movie['url']
            print("song_page_url: {}".format(song_page_url))
            try:
                song_soup = bs(requests.get(song_page_url).text,"lxml")
            except:
                skipped_pages_log.write(song_page_url)
                print("skipped song page: ",song_page_url)
                continue
            
            
            song_list_data = getSongList(song_soup)
            print(song_list_data)
            song_data_list = []
            for song in song_list_data:
                print("Processing song: ",song['song_name'])
                song_url = base_url+song['song_url']
                print("song_url: {}".format(song_url))
                try:
                    song_data_soup = bs(requests.get(song_url).text,"lxml")
                except:
                    skipped_pages_log.write(song_url)
                    print("skipped song page: ",song_url)
                    continue
                song_data = getSongData(song_data_soup)
                for k,v in song.items():
                    song_data.update({k:v})
                song_data_list.append(song_data)
                #print(song_data)
            
            dir_name = os.path.join(DATA_PATH,movie['movie_name'])
            
            try:
                os.stat(dir_name)
            except:
                os.mkdir(dir_name)
                 
            for i,song in enumerate(song_data_list):
                for k,v in movie.items():
                    song.update({k:v})
                file_name = os.path.join(dir_name,song['song_name'])+"_"+str(i)+".json"
                with open(file_name,'w') as writer:
                    json.dump(song,writer)
                    
        page_num += 1
        #break
    

Processing: https://www.lyricsmasti.com/songs_for_movie_A.html
https://www.lyricsmasti.com/songs_for_movie_A.html
No. of song movies in this page: 20
Processing movie:  A Flat - 2010
song_page_url: https://www.lyricsmasti.com/3351/songs-of-movie-A-Flat.html
[{'song_url': '/song/7461/lyrics-of-Dil-Kashi.html', 'song_name': 'Dil Kashi'}, {'song_url': '/song/7884/lyrics-of-Meetha-Sa.html', 'song_name': 'Meetha Sa'}, {'song_url': '/song/7885/lyrics-of-Chal-Halke-Halke.html', 'song_name': 'Chal Halke Halke'}, {'song_url': '/song/7886/lyrics-of-Pyar-Itna-Na-Kar.html', 'song_name': 'Pyar Itna Na Kar'}]
Processing song:  Dil Kashi
song_url: https://www.lyricsmasti.com/song/7461/lyrics-of-Dil-Kashi.html
Processing song:  Meetha Sa
song_url: https://www.lyricsmasti.com/song/7884/lyrics-of-Meetha-Sa.html
Processing song:  Chal Halke Halke
song_url: https://www.lyricsmasti.com/song/7885/lyrics-of-Chal-Halke-Halke.html
Processing song:  Pyar Itna Na Kar
song_url: https://www.lyricsmasti.com/song/78

[{'song_url': '/song/5816/lyrics-of-Aa-Ab-Laut-Chalen.html', 'song_name': 'Aa Ab Laut Chalen'}, {'song_url': '/song/5817/lyrics-of-Mera-Dil-Tera-Deewana.html', 'song_name': 'Mera Dil Tera Deewana'}, {'song_url': '/song/5818/lyrics-of-O-Yaaron-Maaf-Karna.html', 'song_name': 'O Yaaron Maaf Karna'}, {'song_url': '/song/5819/lyrics-of-Yeh-Hai-Pyar.html', 'song_name': 'Yeh Hai Pyar'}, {'song_url': '/song/5820/lyrics-of-Yeh-Kaisi-Mulaqat.html', 'song_name': 'Yeh Kaisi Mulaqat'}]
Processing song:  Aa Ab Laut Chalen
song_url: https://www.lyricsmasti.com/song/5816/lyrics-of-Aa-Ab-Laut-Chalen.html
Processing song:  Mera Dil Tera Deewana
song_url: https://www.lyricsmasti.com/song/5817/lyrics-of-Mera-Dil-Tera-Deewana.html
Processing song:  O Yaaron Maaf Karna
song_url: https://www.lyricsmasti.com/song/5818/lyrics-of-O-Yaaron-Maaf-Karna.html
Processing song:  Yeh Hai Pyar
song_url: https://www.lyricsmasti.com/song/5819/lyrics-of-Yeh-Hai-Pyar.html
Processing song:  Yeh Kaisi Mulaqat
song_url: https:

Processing song:  Bahut Jataate Ho Chaah Ham Se
song_url: https://www.lyricsmasti.com/song/6058/lyrics-of-Bahut-Jataate-Ho-Chaah-Ham-Se.html
Processing song:  Bul-bul Ne Bhi Yu Gul Ko
song_url: https://www.lyricsmasti.com/song/6059/lyrics-of-Bul-bul-Ne-Bhi-Yu-Gul-Ko.html
Processing song:  Mat Kar Itana Gharoor
song_url: https://www.lyricsmasti.com/song/6060/lyrics-of-Mat-Kar-Itana-Gharoor.html
Processing song:  Mehandi Lagaane Ki Raat Aa Gayi
song_url: https://www.lyricsmasti.com/song/6061/lyrics-of-Mehandi-Lagaane-Ki-Raat-Aa-Gayi.html
Processing movie:  Aadmi Sadak Ka - 1977
song_page_url: https://www.lyricsmasti.com/713/songs-of-movie-Aadmi-Sadak-Ka.html
[{'song_url': '/song/6626/lyrics-of-Aaj-Mere-Yaar-Ki-Shadi-Hai.html', 'song_name': 'Aaj Mere Yaar Ki Shadi Hai'}, {'song_url': '/song/6627/lyrics-of-Koi-Kaam-Nahin-Hai-Mushkil.html', 'song_name': 'Koi Kaam Nahin Hai Mushkil'}, {'song_url': '/song/8062/lyrics-of-Falsafa.html', 'song_name': 'Falsafa'}]
Processing song:  Aaj Mere Yaar K

[{'song_url': '/song/6171/lyrics-of-Gulfisha-Gulfisha.html', 'song_name': 'Gulfisha Gulfisha'}, {'song_url': '/song/6203/lyrics-of-Ishq-ada-hai.html', 'song_name': 'Ishq ada hai'}, {'song_url': '/song/6228/lyrics-of-Gumsum-Gumsum-Hum-Tum.html', 'song_name': 'Gumsum Gumsum Hum Tum'}, {'song_url': '/song/6229/lyrics-of-Hai-Dard-Phaila-Hai-Zakhm-Gehra.html', 'song_name': 'Hai Dard Phaila Hai Zakhm Gehra'}, {'song_url': '/song/6266/lyrics-of-Meherbaan.html', 'song_name': 'Meherbaan'}]
Processing song:  Gulfisha Gulfisha
song_url: https://www.lyricsmasti.com/song/6171/lyrics-of-Gulfisha-Gulfisha.html
Processing song:  Ishq ada hai
song_url: https://www.lyricsmasti.com/song/6203/lyrics-of-Ishq-ada-hai.html
Processing song:  Gumsum Gumsum Hum Tum
song_url: https://www.lyricsmasti.com/song/6228/lyrics-of-Gumsum-Gumsum-Hum-Tum.html
Processing song:  Hai Dard Phaila Hai Zakhm Gehra
song_url: https://www.lyricsmasti.com/song/6229/lyrics-of-Hai-Dard-Phaila-Hai-Zakhm-Gehra.html
Processing song:  Me

Processing song:  Na Aadami Ka Koi Bharosa
song_url: https://www.lyricsmasti.com/song/1714/lyrics-of-Na-Aadami-Ka-Koi-Bharosa.html
Processing movie:  Aadmi Aur Insaan - 1969
song_page_url: https://www.lyricsmasti.com/2312/songs-of-movie-Aadmi-Aur-Insaan.html
[{'song_url': '/song/4398/lyrics-of-Ho-neele-parbaton-ki-dhaara.html', 'song_name': 'Ho neele parbaton ki dhaara'}, {'song_url': '/song/4399/lyrics-of-Zindagi-Ke-Rang.html', 'song_name': 'Zindagi Ke Rang'}, {'song_url': '/song/4400/lyrics-of-Zindagi-Ittafaaq-Hain.html', 'song_name': 'Zindagi Ittafaaq Hain'}]
Processing song:  Ho neele parbaton ki dhaara
song_url: https://www.lyricsmasti.com/song/4398/lyrics-of-Ho-neele-parbaton-ki-dhaara.html
Processing song:  Zindagi Ke Rang
song_url: https://www.lyricsmasti.com/song/4399/lyrics-of-Zindagi-Ke-Rang.html
Processing song:  Zindagi Ittafaaq Hain
song_url: https://www.lyricsmasti.com/song/4400/lyrics-of-Zindagi-Ittafaaq-Hain.html
Processing movie:  Aadmi Khilona Hai - 1993
song_page_ur

...

Processing movie:  Awara - 1951
song_page_url: https://www.lyricsmasti.com/22/songs-of-movie-Awara.html
[{'song_url': '/song/22/lyrics-of-Awara-Hoon.html', 'song_name': 'Awara Hoon'}, {'song_url': '/song/23/lyrics-of-Dam-Bhar-Jo-Udhar-Munh-Phere.html', 'song_name': 'Dam Bhar Jo Udhar Munh Phere'}, {'song_url': '/song/181/lyrics-of-Awara-Huun.html', 'song_name': 'Awara Huun'}, {'song_url': '/song/182/lyrics-of-Ab-Raat-Guzarne-Wali-Hai.html', 'song_name': 'Ab Raat Guzarne Wali Hai'}, {'song_url': '/song/1747/lyrics-of-Hum-Tujhse-Mohabbat-Kar-Ke.html', 'song_name': 'Hum Tujhse Mohabbat Kar Ke'}, {'song_url': '/song/1748/lyrics-of-Ek-Bewafa-Se-Pyaar-Kiya.html', 'song_name': 'Ek Bewafa Se Pyaar Kiya'}, {'song_url': '/song/1750/lyrics-of-Ghar-Aaya-Mera-Pardesi.html', 'song_name': 'Ghar Aaya Mera Pardesi'}, {'song_url': '/song/1751/lyrics-of-Jab-Se-Balam-Ghar-Aaye.html', 'song_name': 'Jab Se Balam Ghar Aaye'}]
Processing song:  Awara Hoon
song_url: https://www.lyricsmasti.com/song/22/lyrics-o

Processing song:  Pee Ke Daras Ko Taras Rahin
song_url: https://www.lyricsmasti.com/song/1629/lyrics-of-Pee-Ke-Daras-Ko-Taras-Rahin.html
Processing song:  Kitani Jawaan Hai Raat
song_url: https://www.lyricsmasti.com/song/1630/lyrics-of-Kitani-Jawaan-Hai-Raat.html
Processing movie:  Azadi - 1990
song_page_url: https://www.lyricsmasti.com/3779/songs-of-movie-Azadi.html
[{'song_url': '/song/8769/lyrics-of-Sayonee.html', 'song_name': 'Sayonee'}]
Processing song:  Sayonee
song_url: https://www.lyricsmasti.com/song/8769/lyrics-of-Sayonee.html
Processing movie:  Azhar - 2016
song_page_url: https://www.lyricsmasti.com/3826/songs-of-movie-Azhar.html
[{'song_url': '/song/8896/lyrics-of-Bol-Do-Na-Zara.html', 'song_name': 'Bol Do Na Zara'}, {'song_url': '/song/8897/lyrics-of-Itni-Si-Baat-Hain.html', 'song_name': 'Itni Si Baat Hain'}, {'song_url': '/song/8898/lyrics-of-Oye-Oye.html', 'song_name': 'Oye Oye'}, {'song_url': '/song/8899/lyrics-of-Tu-Hi-Na-Jaane.html', 'song_name': 'Tu Hi Na Jaane'}, {'

Processing song:  Mahiyaa
song_url: https://www.lyricsmasti.com/song/4627/lyrics-of-Mahiyaa.html
Processing song:  Mahiya-Remix
song_url: https://www.lyricsmasti.com/song/4660/lyrics-of-Mahiya-Remix.html
Processing song:  Maula maula
song_url: https://www.lyricsmasti.com/song/4781/lyrics-of-Maula-maula.html
Processing movie:  Aya Sawan Jhoom Ke - 1969
song_page_url: https://www.lyricsmasti.com/476/songs-of-movie-Aya-Sawan-Jhoom-Ke.html
[]
Processing movie:  Aye Mere Watan Ke Logo - 1963
song_page_url: https://www.lyricsmasti.com/3400/songs-of-movie-Aye-Mere-Watan-Ke-Logo.html
[{'song_url': '/song/7565/lyrics-of-Aye-Mere-Watan-Ke-Logo.html', 'song_name': 'Aye Mere Watan Ke Logo'}]
Processing song:  Aye Mere Watan Ke Logo
song_url: https://www.lyricsmasti.com/song/7565/lyrics-of-Aye-Mere-Watan-Ke-Logo.html
Processing movie:  Ayee Milan Ki Bela - 1964
song_page_url: https://www.lyricsmasti.com/353/songs-of-movie-Ayee-Milan-Ki-Bela.html
[{'song_url': '/song/5052/lyrics-of-Pyar-ankhon-se-dh

Processing movie:  Awara - 1951
song_page_url: https://www.lyricsmasti.com/22/songs-of-movie-Awara.html
[{'song_url': '/song/22/lyrics-of-Awara-Hoon.html', 'song_name': 'Awara Hoon'}, {'song_url': '/song/23/lyrics-of-Dam-Bhar-Jo-Udhar-Munh-Phere.html', 'song_name': 'Dam Bhar Jo Udhar Munh Phere'}, {'song_url': '/song/181/lyrics-of-Awara-Huun.html', 'song_name': 'Awara Huun'}, {'song_url': '/song/182/lyrics-of-Ab-Raat-Guzarne-Wali-Hai.html', 'song_name': 'Ab Raat Guzarne Wali Hai'}, {'song_url': '/song/1747/lyrics-of-Hum-Tujhse-Mohabbat-Kar-Ke.html', 'song_name': 'Hum Tujhse Mohabbat Kar Ke'}, {'song_url': '/song/1748/lyrics-of-Ek-Bewafa-Se-Pyaar-Kiya.html', 'song_name': 'Ek Bewafa Se Pyaar Kiya'}, {'song_url': '/song/1750/lyrics-of-Ghar-Aaya-Mera-Pardesi.html', 'song_name': 'Ghar Aaya Mera Pardesi'}, {'song_url': '/song/1751/lyrics-of-Jab-Se-Balam-Ghar-Aaye.html', 'song_name': 'Jab Se Balam Ghar Aaye'}]
Processing song:  Awara Hoon
song_url: https://www.lyricsmasti.com/song/22/lyrics-o

Processing song:  Pee Ke Daras Ko Taras Rahin
song_url: https://www.lyricsmasti.com/song/1629/lyrics-of-Pee-Ke-Daras-Ko-Taras-Rahin.html
Processing song:  Kitani Jawaan Hai Raat
song_url: https://www.lyricsmasti.com/song/1630/lyrics-of-Kitani-Jawaan-Hai-Raat.html
Processing movie:  Azadi - 1990
song_page_url: https://www.lyricsmasti.com/3779/songs-of-movie-Azadi.html
[{'song_url': '/song/8769/lyrics-of-Sayonee.html', 'song_name': 'Sayonee'}]
Processing song:  Sayonee
song_url: https://www.lyricsmasti.com/song/8769/lyrics-of-Sayonee.html
Processing movie:  Azhar - 2016
song_page_url: https://www.lyricsmasti.com/3826/songs-of-movie-Azhar.html
[{'song_url': '/song/8896/lyrics-of-Bol-Do-Na-Zara.html', 'song_name': 'Bol Do Na Zara'}, {'song_url': '/song/8897/lyrics-of-Itni-Si-Baat-Hain.html', 'song_name': 'Itni Si Baat Hain'}, {'song_url': '/song/8898/lyrics-of-Oye-Oye.html', 'song_name': 'Oye Oye'}, {'song_url': '/song/8899/lyrics-of-Tu-Hi-Na-Jaane.html', 'song_name': 'Tu Hi Na Jaane'}, {'